In [17]:
import os
import re
from datetime import timedelta

import pandas as pd
import numpy as np

import matplotlib.pyplot as plt

import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [21]:
pd.options.plotting.backend = "plotly"
template = "plotly_dark"

In [4]:
def load_price_timeseries(file: str) -> pd.Series:
    df = pd.read_csv(file)
    df.index = pd.to_datetime(df["Date"], format="%d/%m/%Y %H:%M")
    return df["Intraday Continuous 15 minutes ID1-Price"]  # * 1e-6 # €/MWh -> €/Wh

In [5]:
def load_results(dir):
    res = {}
    files = [f for f in os.listdir(dir) if f.endswith(".parquet")]
    for file in files:
        name, _ = os.path.splitext(file)
        res[name] = pd.read_parquet(dir + file)

    return res

In [11]:
def calc_fec(df):
    power = df["power_sim"]
    power_pos = power[power > 0].sum() * (1/60)
    power_neg = power[power < 0].abs().sum() * (1/60)
    return (power_pos + power_neg) / 2 / 180e3

In [12]:
def calc_roundtrip_efficiency(res):
    p = res["power_sim"]
    e_pos = p[p > 0].abs().sum() * (1/60)  # Wh
    e_neg = p[p < 0].abs().sum() * (1/60)  # Wh

    delta_soc = res["soc_sim"].iloc[-1] - res["soc_sim"].iloc[0]
    delta_e = delta_soc * 180e3  # Wh

    return abs(e_neg) / (e_pos - delta_e)

In [13]:
def calc_revenue(df, price):
    price = price.resample(timedelta(minutes=1)).ffill()
    df = df.join(price)
    return -1 * sum(df["power_sim"] * df["Intraday Continuous 15 minutes ID1-Price"]) * (1/60) * 1e-6  # W -> MWh

In [14]:
price = load_price_timeseries("data/intraday_prices/electricity_prices_germany_2021.csv")

In [25]:
res = load_results("results/")

In [27]:
for dt in (5, 15):
    df = res[f"2021 NL r=3.0 r_opt=3.0 {dt}min"]
    eff = calc_roundtrip_efficiency(df)
    fec = calc_fec(df)
    rev = calc_revenue(df, price)
    srev = rev/fec
    print(f"{dt=} {eff=:.2%} {fec=:.2f} {rev=:.2f}€ {srev=:.2f}€")

df = res[f"2021 LP r=3.0 eff=0.9"]
eff = calc_roundtrip_efficiency(df)
fec = calc_fec(df)
rev = calc_revenue(df, price)
srev = rev/fec
print(f"{dt=} {eff=:.2%} {fec=:.2f} {rev=:.2f}€ {srev=:.2f}€")

dt=5 eff=87.19% fec=27.37 rev=223.95€ srev=8.18€
dt=15 eff=87.49% fec=27.39 rev=223.19€ srev=8.15€
dt=15 eff=85.81% fec=26.44 rev=222.44€ srev=8.41€


In [23]:
pd.DataFrame(
    data={
        "soc_sim - 5min": res["2021 NL r=1.0 r_opt=1.0 5min"]["soc_sim"],
        "soc_sim - 15min": res["2021 NL r=1.0 r_opt=1.0 15min"]["soc_sim"],
        "soc_opt - 5min": res["2021 NL r=1.0 r_opt=1.0 5min"]["soc_opt"],
        "soc_opt - 15min": res["2021 NL r=1.0 r_opt=1.0 15min"]["soc_opt"],
    },
    index = res["2021 NL r=1.0 r_opt=1.0 5min"].index
).plot(template=template)

In [24]:
pd.DataFrame(
    data={
        "power_sim - 5min": res["2021 NL r=1.0 r_opt=1.0 5min"]["power_sim"],
        "power_sim - 15min": res["2021 NL r=1.0 r_opt=1.0 15min"]["power_sim"],
        "power_opt - 5min": res["2021 NL r=1.0 r_opt=1.0 5min"]["power_opt"],
        "power_opt - 15min": res["2021 NL r=1.0 r_opt=1.0 15min"]["power_opt"],
    },
    index = res["2021 NL r=1.0 r_opt=1.0 5min"].index
).plot(template=template)